# Monitorare

In [ ]:
import pandas as pd
import numpy as np
import time
from datetime import datetime, timedelta
import tpqoa

Il codice fino ad ora

In [ ]:
class Trader(tpqoa.tpqoa):
    
    def __init__(self,config_file, instrument, period, window, units):
        super().__init__(config_file)
        self.instrument = instrument
        self.period=period
        self.tickData = pd.DataFrame()
        self.rawData = None 
        self.ultimoPeriodo = None 
        self.data = None
        self.units = units
        self.posizione = 0
        
        ########################## STRATEGY SPECIFIC ATTRIBUTES ##############################
        self.window = window
        
    def getMostRecent(self, days=5): 
        '''questo metodo scarica i dati FINO ad adesso'''
        while True:
            now = datetime.now(timezone.utc)
            now = now - timedelta(microseconds = now.microsecond) # pay attention, microseconds and then microsecond (singular!!!)
            yesterday = now - timedelta(days= days) # lo chiamo YESTERDAY, ma è l'inizio del periodo da scaricare
            df = self.get_history(instrument = self.instrument, start = str(yesterday)[:-6], end = str(now)[:-6],
                        granularity= "S5", price="M", localize=False)["c"].to_frame() 
                        # scarico a 5secondi, il che vuol dire che period non può essere più corto!
            df.rename(columns={"c":self.instrument},inplace=True)
            self.rawData = df.resample(self.period, label="right").last().dropna().iloc[:-1]
            self.ultimoPeriodo = self.rawData.index[-1]
            if pd.to_datetime(datetime.now(timezone.utc)) - self.ultimoPeriodo < pd.to_timedelta(self.period):
                break
            else:
                time.sleep(2)
    
    def on_success(self, time, bid, ask):
        print(self.ticks, end=" ")
        tickCorrente = pd.to_datetime(time)
        df = pd.DataFrame({self.instrument:(ask+bid)/2}, index=[tickCorrente])
        self.tickData=pd.concat((self.tickData,df),axis=0)
        if tickCorrente - self.ultimoPeriodo > pd.to_timedelta(self.period):
            self.resampleJoin()
            self.defineStrategy()
            self.executeTrade()
    
    def resampleJoin(self):
        self.rawData=pd.concat((self.rawData,self.tickData.resample(self.period,label="right").last().ffill().iloc[:-1] ),axis=0)
        self.tickData = self.tickData.iloc[-1:] 
        self.ultimoPeriodo = self.rawData.index[-1] 
        
    def defineStrategy(self):
        df = self.rawData.copy()
        df["logRet"]=np.log(df[self.instrument] / df[self.instrument].shift(1))
        df["posizione"]= - np.sign(df.logRet.rolling(self.window).mean())
        self.data = df.copy()
        
    def executeTrade(self):
        if self.data.posizione.iloc[-1] == 1: # andiamo lunghi
            if self.posizione == 0:
                order = self.create_order(instrument = self.instrument, units = self.units, suppress=True, ret = True)
                print("VADO LUNGO",self.units,order["price"])
            elif self.posizione == -1:
                order = self.create_order(instrument = self.instrument, units = 2*self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE CORTA E VADO LUNGO",2*self.units,order["price"])
            self.posizione=1
        elif self.data.posizione.iloc[-1] == -1: # andiamo corti
            if self.posizione == 0:
                order = self.create_order(instrument = self.instrument, units = -self.units, suppress=True, ret = True)
                print("VADO CORTO",-self.units,order["price"])
            elif self.posizione == 1:
                order = self.create_order(instrument = self.instrument, units = -2*self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE LUNGA E VADO CORTO",-2*self.units,order["price"])
            self.posizione=-1
        elif self.data.posizione.iloc[-1] == 0: # andiamo neutri
            if self.posizione == 1:
                order = self.create_order(instrument = self.instrument, units = -self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE LUNGA",-self.units,order["price"])
            elif self.posizione == -1:
                order = self.create_order(instrument = self.instrument, units = self.units, suppress=True, ret = True)
                print("CHIUDO POSIZIONE CORTA",self.units,order["price"])
            self.posizione=0
        

Aggiungiamo un metodo report_trade e modifichiamo i print in execute_trade

In [ ]:
trader = Trader("oandaMY.cfg","EUR_USD","1min", window=1, units=100000)

In [ ]:
print(datetime.now(timezone.utc))
trader.getMostRecent()
trader.stream_data(trader.instrument,stop=150)

Inseriamo la chiusura finale in stream_data direttamente

In [ ]:
trader.stream_data??

In [ ]:
trader = Trader("oandaMY.cfg","EUR_USD","1min", window=1, units=100000)

In [ ]:
print(datetime.now(timezone.utc))
trader.getMostRecent()
trader.stream_data(trader.instrument,stop=150)